In [40]:
import importlib
import json
import re

import mtg.core as mtg
importlib.reload(mtg)

<module 'mtg.core' from '/Users/oichii/Desktop/code/python/mtg-card-parser/mtg/core.py'>

In [48]:
s = 'Draw two cards'
r = 'Draw (.+) cards'
print(re.match(r, s).groups()[0])

two


In [37]:
data = json.loads(open('cards.json', 'r').read())

In [38]:
cards: list[mtg.Card] = []
for chunk in data:
    if 'card_faces' in chunk.keys():
        continue
    if chunk['set_name'].startswith('Un') or chunk['set'].startswith('cmb'):
        continue
    try:
        cards += [mtg.Card.from_json(chunk)]
        cards[len(cards)-1].orig = chunk
    except:
        print(json.dumps(chunk, indent=4))

In [26]:
def get_card(name):
    for card in cards:
        if card.name == name:
            return card

def parse_card(name):
    card = get_card(name)
    mtg.CardText.parse(card.text)

In [27]:
# get_card('Kalitas, Bloodchief of Ghet').print()

parse_card('Sorin, Grim Nemesis')

+1: Reveal the top card of your library and put that card into your hand. Each opponent loses life equal to its mana value.
[
    [
        {
            "type": "UNKNOWN_COST"
        }
    ]
]
−X: [CARDNAME] deals X damage to target creature or planeswalker and you gain X life.
[
    [
        {
            "type": "UNKNOWN_COST"
        }
    ]
]
−9: Create a number of 1/1 black Vampire Knight creature tokens with lifelink equal to the highest life total among all players.
[
    [
        {
            "type": "UNKNOWN_COST"
        }
    ]
]


In [41]:
for card in cards:
    # print(card.text)
    print(f' === {card.name} ===')
    t = mtg.CardText.parse(card.text)
    print('----')

 === Static Orb ===
----
 === Sensory Deprivation ===
----
 === Road of Return ===
----
 === Storm Crow ===
----
 === Walking Sponge ===
{T}: Target creature loses your choice of flying, first strike, or trample until end of turn.
[
    [
        {
            "type": "tap"
        }
    ]
]
----
 === Ravnica at War ===
----
 === Torrent of Fire ===
----
 === Wyluli Wolf ===
{T}: Target creature gets +1/+1 until end of turn.
[
    [
        {
            "type": "tap"
        }
    ]
]
----
 === Pteramander ===
{7}{U}: Adapt 4. This ability costs {1} less to activate for each instant and %s0% in your graveyard. 
[
    [
        {
            "type": "mana_cost",
            "pips": [
                {
                    "type": "generic",
                    "amount": 7
                },
                {
                    "type": "colored_mana",
                    "color": "U"
                }
            ]
        }
    ]
]
----
 === Nantuko Elder ===
{T}: Add {C}{G}.
[
    [
 

In [29]:
def regex_search(regex: str):
    for card in cards:
        m = re.match(regex, card.text)
        if not m:
            continue
        print(card.text)
        print(m.groups())


In [30]:
# def card_type_matching(line: str) -> tuple[str, list]:
#     m = re.search(card_types_r, line)
#     if not m:
#         return line, [{
#             'type': 'text',
#             'text': line
#         }]
#     s = m.groups()[0] + 'card'
#     ts = m.groups()[0][:-1].split(', ')
#     splits = line.split(s)
#     result = []
#     result += [{
#         'type': 'text',
#         'text': splits[0]
#     }]
#     result += [{
#         'type': 'card_types',
#         'types': ts
#     }]
#     l, n = card_type_matching(splits[1])

#     if n:
#         result += n
#     return l.replace(s, f'[CONDITION{}]') result

# for card in cards[:100]:
#     lines = card.text.split('\n')
#     for line in lines:
#         print(line)
#         print(json.dumps(card_type_matching(line), indent=4))

In [31]:
for card in cards:
    if card.name == 'Koth of the Hammer':
        card.print()
        break

Koth of the Hammer
	+1: Untap target Mountain. It becomes a 4/4 red Elemental creature until end of turn. It`s still a land.
−2: Add {R} for each Mountain you control.
−5: You get an emblem with "Mountains you control have '{T}: This land deals 1 damage to any target.'"



In [32]:
PARENTHESIS_R = r'(\".+\")'

def parenthesis_matching(line: str) -> tuple[str, list]:
    m = re.search(PARENTHESIS_R, line)
    if not m:
        return line, []
    print(m.groups())
    return line, []

In [33]:
# whenever_r = r'Whenever ([^.]*)\.'
whenever_r = r"Whenever ([^,]+), (.+)."

whenever_common = [
    'attacks',
    'blocks'
]

def whenever_matcher(line: str) -> dict:
    m = re.match(whenever_r, line)
    if not m:
        return {}
    g = m.groups()
    cost = g[0]
    effect = g[1]
    print('Whenever \033[91m{}, \033[92m{}\033[0m.\n'.format(cost, effect))


In [34]:
ability_r = r"(.+): (.+)"

def ability_matcher(line: str) -> dict:
    m = re.match(ability_r, line)
    if not m: return
    g = m.groups()
    print(line)
    costs = mtg.Cost(g[0])
    effect = g[1]
    # TODO

In [35]:
TOKENIZE_FUNCS = [
    card_type_matching,
    parenthesis_matching
]

def tokenize(line: str) -> tuple[str, list]:
    res_line = line
    res_arr = []
    for f in TOKENIZE_FUNCS:
        res_line, a = f(res_line)
        res_arr += a
    return res_line, res_arr

NameError: name 'card_type_matching' is not defined

In [ ]:
for card in cards[:500]:
    lines = card.text.split('\n')
    for line in lines:
        if line == '': continue
        if line.count(',') < 2: continue
        l, a = tokenize(line)
        ability_matcher(l)


{T}: Target creature loses your choice of flying, first strike, or trample until end of turn.
[
    {
        "type": "tap"
    }
]
{B}{B}{B}, {T}: Destroy target creature. If that creature dies this way, create a black Vampire creature token. Its power is equal to that creature's power and its toughness is equal to that creature's toughness.
[
    {
        "type": "mana_cost",
        "pips": [
            "B",
            "B",
            "B"
        ]
    },
    {
        "type": "tap"
    }
]
{W}{U}{B}{R}{G}, {T}, Sacrifice [CARDNAME]: Draw three cards.
[
    {
        "type": "mana_cost",
        "pips": [
            "W",
            "U",
            "B",
            "R",
            "G"
        ]
    },
    {
        "type": "tap"
    },
    {
        "type": "UNKNOWN_COST"
    }
]
{4}, {T}: Look at the top card of your library. If it's a %0%, you may put it onto the battlefield tapped. If you don't put the card onto the battlefield, you may put it on the bottom of your library

ValueError: invalid literal for int() with base 10: 'T'

In [ ]:
for card in cards:
    if '{' in card.text:
        print(card.text + '\n')

Choose one —
• Return target permanent card from your graveyard to your hand.
• Put your commander into your hand from the command zone.
Entwine {2} (Choose both if you pay the entwine cost.)

{T}: Target creature loses your choice of flying, first strike, or trample until end of turn.

{T}: Target creature gets +1/+1 until end of turn.

Flying
{7}{U}: Adapt 4. This ability costs {1} less to activate for each instant and sorcery card in your graveyard. (If this creature has no +1/+1 counters on it, put four +1/+1 counters on it.)

{T}: Add {C}{G}.

{2}{B}, Sacrifice a creature: Create two Treasure tokens.
Sacrifice three Treasures: Draw a card.

Flying
When [CARDNAME] enters the battlefield, untap up to seven lands.
{2}{U}{U}: Return [CARDNAME] to its owner's hand.

{T}: Put target creature card from your graveyard on top of your library. Activate only during your turn, before attackers are declared.

Swampwalk (This creature can't be blocked as long as defending player controls a Swam

In [ ]:
s = '{W}{W}'
a = mtg.Cost.parse(s)

AttributeError: type object 'Cost' has no attribute 'parse'